In [1]:
# Librerias utiles
import pandas as pd 
import numpy as np 
import matplotlib.pyplot as plt 
import plotly
#import seaborn as sns 
import plotly.express as px
import missingno as msno
import plotly.io as pio
import plotly.graph_objects as go
from mapsmx import MapsMX
import geopandas
import pyproj
import json
#sns.set_theme()

In [2]:
state = MapsMX().get_geo('state')
muns = MapsMX().get_geo('municipality')
yuc = muns[muns['cve_ent']=='31']

In [18]:
victimas = pd.read_csv('reportes/reporte_semujeres_21_DICIEMBRE_2021.csv',low_memory=False, dtype={'pk_perfil_agresor': 'object','num_hijos':'int32'}, parse_dates=['fecha_recepcion','fecha_hechos'])

In [19]:
victimas.modalidad.unique()

array(['Familiar', 'En la comunidad', 'Laboral', 'Institucional',
       'Escolar/Docente', 'Digital/Cibernética', 'Política'], dtype=object)

In [30]:
victimas['Tipo de vínculo con victima'].unique()

array(['Otro', 'En la comunidad', 'Familiar', 'Laboral y docente'],
      dtype=object)

In [31]:
victimas[victimas['Tipo de vínculo con victima']=='En la comunidad'].shape

(221, 49)

In [20]:
#victimas = victimas[(victimas['Dependencia de recepcion'].str.contains('MUJERES')==True)&(victimas.fecha_hechos>='01-01-2021')&(victimas.fecha_hechos<='09-30-2021')]
victimas = victimas[(victimas.fecha_hechos>='01-01-2021')&(victimas.fecha_hechos<='12-31-2021')&(victimas.modalidad=='En la comunidad')]
victimas.shape

(377, 49)

In [16]:
conapo = pd.read_csv('conapo.csv')

In [17]:
conapo = (conapo[(conapo['CLAVE_ENT']==31)&(conapo['AÑO']==2021)&(conapo['SEXO']=='Mujeres')]).reset_index(drop=True)
conapo = conapo[['MUN','POB']]
conapo = conapo.groupby('MUN').sum()
conapo

POB
MUN              
Abalá        3467
Acanceh      8777
Akil         6105
Baca         3280
Bokobá       1163
...           ...
Valladolid  43897
Xocchel      1845
Yaxcabá      7981
Yaxkukul     1721
Yobaín       1203

[106 rows x 1 columns]

In [31]:
"""inegi_2020 = pd.read_csv('censo_yuc.csv')
pob_fem = inegi_2020[inegi_2020.NOM_LOC=='Total del Municipio'][['MUN','NOM_MUN','POBFEM' ]].reset_index(drop=True)
pob_fem.POBFEM.astype(int).sum()"""

"inegi_2020 = pd.read_csv('censo_yuc.csv')\npob_fem = inegi_2020[inegi_2020.NOM_LOC=='Total del Municipio'][['MUN','NOM_MUN','POBFEM' ]].reset_index(drop=True)\npob_fem.POBFEM.astype(int).sum()"

In [21]:
casos_mun = victimas.groupby('municipiohechos')['fk_euv'].count()
casos_mun = yuc[['geometry_mun','nom_mun']].merge(casos_mun, right_on=casos_mun.index, left_on='nom_mun', how='left')
casos_mun.fillna(0,inplace=True)
casos_mun = pd.DataFrame(casos_mun.merge(conapo,left_on='nom_mun',right_on=conapo.index,how='left'))
casos_mun[['fk_euv','POB']] = casos_mun[['fk_euv','POB']].astype(int)
casos_mun['Tasa 1000'] = round(casos_mun.fk_euv/casos_mun.POB*1000,2)
gdf = geopandas.GeoDataFrame(casos_mun, geometry='geometry_mun')
gdf = gdf.set_index('nom_mun')
gdf = gdf.to_crs(pyproj.CRS.from_epsg(4326))

In [22]:
poly_json = json.loads(gdf.geometry_mun.to_json())

In [23]:
gdf

geometry_mun  fk_euv    POB  \
nom_mun                                                                        
Abalá       POLYGON ((-89.66875 20.72618, -89.65565 20.711...       1   3467   
Acanceh     POLYGON ((-89.45571 20.91324, -89.45216 20.908...       0   8777   
Akil        POLYGON ((-89.35315 20.32405, -89.35300 20.323...       2   6105   
Baca        POLYGON ((-89.41583 21.22625, -89.40978 21.225...       0   3280   
Bokobá      POLYGON ((-89.16865 21.05597, -89.16863 21.055...       0   1163   
...                                                       ...     ...    ...   
Valladolid  POLYGON ((-87.97314 20.87887, -87.97370 20.877...       7  43897   
Xocchel     POLYGON ((-89.08540 20.84566, -89.08665 20.839...       0   1845   
Yaxcabá     POLYGON ((-88.71779 20.76206, -88.71193 20.755...       6   7981   
Yaxkukul    POLYGON ((-89.43052 21.08952, -89.42991 21.089...       0   1721   
Yobaín      POLYGON ((-89.06922 21.36331, -89.07006 21.359...       0   1203   

            Tasa 1000  
nom_mun                
Abalá            0.29  
Acanceh          0.00  
Akil             0.33  
Baca             0.00  
Bokobá           0.00  
...               ...  
Valladolid       0.16  
Xocchel          0.00  
Yaxcabá          0.75  
Yaxkukul         0.00  
Yobaín           0.00  

[106 rows x 4 columns]

In [33]:
fig = px.choropleth_mapbox(gdf, geojson=gdf.geometry_mun, 
                    locations=gdf.index, color='Tasa 1000',
                    color_continuous_scale="Viridis",
                    labels = {'nom_mun':'Municipio', 'fk_euv':'Casos','POB':'Pob. Fem. 2021'},
                    hover_data={'POB':True,'fk_euv':True},
                    #title='Mapa 2. Feminicidios Registrados por Municipio',
                    #color_continuous_midpoint=np.average(gdf['municipioV'], weights=gdf['POBFEM'].astype(int)),
                    center={"lat": 20.400417, "lon": -89.134857},
                    mapbox_style="carto-positron", 
                    zoom=7.5,
                    #opacity=0.5,
                    title='Tasa de violencia en la comunidad por cada 1000 mujeres (proyecciones CONAPO 2021)',
                    )
fig.update_geos(fitbounds="locations", visible=False)

#fig.update_layout(xaxis=dict(domain=[0, 0.5]), yaxis=dict(domain=[0.25, 0.75]))

fig.add_annotation(
    # The arrow head will be 25% along the x axis, starting from the left
    x=0,
    # The arrow head will be 40% along the y axis, starting from the bottom
    y=0.98,
    text="<b>Temporalidad:</b> {}<br><b>Casos Ocurridos:</b> {}".format(2021,gdf['fk_euv'].sum()),
    showarrow=False,
    bordercolor="black",
    bgcolor="white",
    borderwidth=1.5,
    opacity=0.8
)

#fig.update(layout = dict(title=dict(x=0.5)))
fig.update_layout(height=600)
print(fig.data[0].hovertemplate)
#fig.update_traces(hovertemplate='Municipio=%{location}<br>Agresores Armados=%{customdata[0]}<extra></extra>')
#pio.write_html(fig, file='../docs/figs/comunidad_conapo_2021.html', include_plotlyjs='cdn', full_html=False)
fig.show()

Municipio=%{location}<br>Pob. Fem. 2021=%{customdata[0]}<br>Casos=%{customdata[1]}<br>Tasa 1000=%{z}<extra></extra>


In [34]:
gdf.sort_values('Tasa 1000', ascending=False).head(10)

geometry_mun  fk_euv  \
nom_mun                                                                      
Cuncunul         POLYGON ((-88.37132 20.69086, -88.37124 20.687...       1   
Mocochá          POLYGON ((-89.44375 21.18594, -89.44374 21.185...       2   
Telchac Puerto   POLYGON ((-89.22729 21.33696, -89.22765 21.333...       1   
Sanahcat         POLYGON ((-89.19186 20.77862, -89.19204 20.774...       1   
Tekax            POLYGON ((-89.07855 20.34599, -89.08182 20.334...      24   
Conkal           POLYGON ((-89.52137 21.11592, -89.52135 21.115...       6   
Yaxcabá          POLYGON ((-88.71779 20.76206, -88.71193 20.755...       6   
Dzilam de Bravo  POLYGON ((-88.47239 21.47240, -88.47288 21.472...       1   
Sinanché         POLYGON ((-89.16306 21.30751, -89.15816 21.306...       1   
Chapab           POLYGON ((-89.54080 20.57602, -89.54080 20.576...       1   

                   POB  Tasa 1000  
nom_mun                            
Cuncunul           857       1.17  
Mocochá           1758       1.14  
Telchac Puerto     916       1.09  
Sanahcat           923       1.08  
Tekax            23296       1.03  
Conkal            6030       1.00  
Yaxcabá           7981       0.75  
Dzilam de Bravo   1422       0.70  
Sinanché          1634       0.61  
Chapab            1709       0.59